In [196]:
import pandas as pd
import re


In [197]:
df_reports = pd.read_csv('a:/bloeding-met-patientenlijst-gedetailleerd/verslagen-abb-corrected.csv')
df_reports['verslagen_report_start_date'] = pd.to_datetime(df_reports['verslagen_report_start_date'], errors='coerce')

df_reports.head()

pseudo_id             verslagen_report_tags  \
0  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6                   Klinische Brief   
1  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6  Consult, Kliniek: vervolgconsult   
2  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6               Poliklinische Brief   
3  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6               Poliklinische Brief   
4  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6  Consult, Kliniek: vervolgconsult   

                            verslagen_report_content  \
0  Dhr. A.J. Dingemans, huisarts\r\n[STREETNAME] ...   
1  Samenvatting: \nRectaal bloedverlies obv diver...   
2  COLOSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] [L...   
3  GASTROSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] ...   
4  Samenvatting: \nRectaal bloedverlies ; eenmali...   

   verslagen_report_age_at_time_of_event   verslagen_report_specialism  \
0                                     87  Maag-, Darm- en Leverziekten   
1                                     87  Maag-, Darm- en Leverziekten   
2                                     87  Maag-, Darm- en Leverziekten   
3                                     87  Maag-, Darm- en Leverziekten   
4                                     87  Maag-, Darm- en Leverziekten   

  verslagen_report_start_date  \
0         2020-11-26 15:06:00   
1         2020-11-26 09:53:00   
2         2020-11-25 14:13:00   
3         2020-11-25 13:48:00   
4         2020-11-25 08:47:00   

                             abbreviations_corrected  
0  meneer a.j. dingemans, huisarts\r\n[streetname...  
1  samenvatting: \nrectaal bloedverlies onder beg...  
2  coloscopie\r\n\r\nbetreft\r\nmevrouw [initials...  
3  gastroscopie\r\n\r\nbetreft\r\nmevrouw [initia...  
4  samenvatting: \nrectaal bloedverlies ; eenmali...

In [198]:
df_measures = df_reports[['pseudo_id', 'verslagen_report_start_date', 'verslagen_report_specialism', 'verslagen_report_content']]
df_measures.head()

pseudo_id verslagen_report_start_date  \
0  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 15:06:00   
1  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 09:53:00   
2  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 14:13:00   
3  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 13:48:00   
4  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 08:47:00   

    verslagen_report_specialism  \
0  Maag-, Darm- en Leverziekten   
1  Maag-, Darm- en Leverziekten   
2  Maag-, Darm- en Leverziekten   
3  Maag-, Darm- en Leverziekten   
4  Maag-, Darm- en Leverziekten   

                            verslagen_report_content  
0  Dhr. A.J. Dingemans, huisarts\r\n[STREETNAME] ...  
1  Samenvatting: \nRectaal bloedverlies obv diver...  
2  COLOSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] [L...  
3  GASTROSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] ...  
4  Samenvatting: \nRectaal bloedverlies ; eenmali...

In [199]:
agib_terms = [
    r"\bacute gi\s*bloeding\b",                       # explicit AGIB phrasing
    r"\bacute maagdarmbloeding\b",                    # Dutch GI bleed
    r"\bacute gastro[-\s]?intestinale bloeding\b",    # formal wording
    r"\b agib \b"                                       # abbreviation
]


agib_terms_MDL = agib_terms + [
    r"\bacute bloeding\b",               # can mean GI in MDL context
    r"\bmassaal bloedverlies\b",         # could suggest AGIB if noted by MDL
    r"\bshock door bloeding\b",          # common phrasing in acute cases
    r"\bspoed scopie\b",                 # urgent scope suggests AGIB context
    r"\bhematemesis\b",                  # AGIB if acute presentation
    r"\bmelaena met hypotensie\b"        # combo is a classic AGIB signal
]


gib_terms = [
    r'\bmel[ae]na\b',                        # black tarry stool
    r'\bhematemesis\b',                      # vomiting blood
    r'\bhematochez[iy]e\b',                  # fresh blood per rectum
    r'\brectaal bloed\b',                    # rectal blood
    r'\brectaal verlies\b',                  # rectal blood loss
    r'\bzwart(e)? ontlasting\b',             # black stool
    r'\bbloed in ontlasting\b',              # blood in stool
    r'\bdivertikelbloeding\b',               # bleeding from diverticula
    r'\b(bloed)?stolsels\b',                 # clots
    r'\bgastro[-\s]?intestinale bloeding\b', # literal GI bleeding
    r'\bhemorragie\b'                        # hemorrhage (less common)
]

gib_terms_MDL = gib_terms + [
    r'\bbloedverlies\b',               # general blood loss
    r'\bvers bloed per anum\b',        # fresh blood per anus
    r'\bbloedende divertikels?\b',     # bleeding diverticula
    r'\bmaagdarmbloeding\b',           # Dutch variant of GI bleeding
    r'\binvloed van antistolling\b',   # bleeding risk via anticoagulation
    r'\bhemoglobinedaling\b',          # drop in Hb, in GI context implies GIB
    r'\bbloedende ulcus\b',            # bleeding ulcer
    r'\bbloedend varices?\b'           # variceal bleeding
]


scopie_terms = [
    r'\bgastroscopie\b', r'\bendoscopie\b', r'\bcoloscopie\b', r'\bercp\b',
    r'\bvideo[-\s]?endoscopie\b', r'\bendoscopisch\b',
    r'\bspoed[-\s]?gastroscopie\b', r'\burgente coloscopie\b'
]


treatment_terms = [
    r'\bpantoprazol\b', 
    r'\bperfusor\b', 
    r'\binfuus\b', 
    r'\btransfusie\b',
    r'\bacenocoumarol\b', 
    r'\bbloeddruk (laag|dalend)\b', 
    r'\bhypotens(ie|ief)\b',
    r'\bvitamine k\b',              # reversal agent for coumarin
    r'\bprotonpompremmer\b',        # class of GI bleed meds
    r'\biv vocht\b',                # fluid support in shock
    r'\bspoedopname\b'              # linked to acute presentation
]




In [200]:
negation_triggers = r"\b(geen|niet|zonder|uitsluiten|ontkent|ontkend|ontkennen|negatief voor|geen aanwijzing voor|kan uitgesloten worden|geen tekenen van|niet passend bij|afwezig|geen bewijs voor|uitsluitend)\b"


In [201]:
def match_terms(text, patterns):
    text = text.lower()
    return any(re.search(pattern, text) for pattern in patterns)
    # text = text.lower()
    # return any(pattern.search(text) for pattern in patterns)


def match_term_per_specialism(df, text_column, terms, terms_MDL,  new_column_name='new_column', specialism_column='verslagen_report_specialism', specialism_value='Maag-, Darm- en Leverziekten'):
    """
    Match terms in a DataFrame column and create a new column with the results.
    """
    # Create a new column with the results
    # df[new_column_name] = df[text_column].apply(lambda x: match_terms(x, terms_MDL) if df[specialism_column][x] == specialism_value else match_terms(x, terms))
    df[new_column_name] = df.apply(
    lambda row: match_terms(row[text_column], terms_MDL) if row[specialism_column] == specialism_value else match_terms(row[text_column], terms),
    axis=1
)
    # # Apply negation check
    # negation = df[text_column].str.contains(negation_triggers, case=False)
    # df.loc[negation, new_column_name] = False
    



In [202]:
match_term_per_specialism(df_measures, 'verslagen_report_content', agib_terms, agib_terms_MDL, new_column_name='has_agib', specialism_column='verslagen_report_specialism', specialism_value='Maag-, Darm- en Leverziekten')
match_term_per_specialism(df_measures, 'verslagen_report_content', gib_terms, gib_terms_MDL, new_column_name='has_gib', specialism_column='verslagen_report_specialism', specialism_value='Maag-, Darm- en Leverziekten')

C:\Users\Y.vanMegen\AppData\Local\Temp\ipykernel_11608\256674290.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[new_column_name] = df.apply(
C:\Users\Y.vanMegen\AppData\Local\Temp\ipykernel_11608\256674290.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[new_column_name] = df.apply(


In [203]:
df_measures['has_agib'].value_counts()

False    10849
True       241
Name: has_agib, dtype: int64

In [204]:
df_measures['has_gib'].value_counts()

False    8307
True     2783
Name: has_gib, dtype: int64

In [205]:
df_measures['has_agib2'] = df_measures['verslagen_report_content'].apply(lambda x: match_terms(x, agib_terms))
df_measures['has_gib_symptoms'] = df_measures['verslagen_report_content'].apply(lambda x: match_terms(x, gib_terms))
df_measures['has_scopie_reference'] = df_measures['verslagen_report_content'].apply(lambda x: match_terms(x, scopie_terms))
df_measures['has_gib_treatment'] = df_measures['verslagen_report_content'].apply(lambda x: match_terms(x, treatment_terms))

df_measures

pseudo_id verslagen_report_start_date  \
0      046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 15:06:00   
1      046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 09:53:00   
2      046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 14:13:00   
3      046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 13:48:00   
4      046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 08:47:00   
...                                         ...                         ...   
11085  FD8C682C1F4FDA1E5EC0B760D30875556419BD71         2015-03-20 08:13:00   
11086  FD8C682C1F4FDA1E5EC0B760D30875556419BD71         2015-01-14 15:39:00   
11087  FD8C682C1F4FDA1E5EC0B760D30875556419BD71         2014-12-21 09:31:00   
11088  FD8C682C1F4FDA1E5EC0B760D30875556419BD71         2010-11-10 21:03:00   
11089  FD8C682C1F4FDA1E5EC0B760D30875556419BD71         2010-11-10 20:29:00   

        verslagen_report_specialism  \
0      Maag-, Darm- en Leverziekten   
1      Maag-, Darm- en Leverziekten   
2      Maag-, Darm- en Leverziekten   
3      Maag-, Darm- en Leverziekten   
4      Maag-, Darm- en Leverziekten   
...                             ...   
11085           Interne Geneeskunde   
11086           Interne Geneeskunde   
11087             Spoedeisende Hulp   
11088             Spoedeisende Hulp   
11089             Spoedeisende Hulp   

                                verslagen_report_content  has_agib  has_gib  \
0      Dhr. A.J. Dingemans, huisarts\r\n[STREETNAME] ...     False     True   
1      Samenvatting: \nRectaal bloedverlies obv diver...     False     True   
2      COLOSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] [L...     False     True   
3      GASTROSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] ...     False     True   
4      Samenvatting: \nRectaal bloedverlies ; eenmali...     False     True   
...                                                  ...       ...      ...   
11085  Samenvatting: \n1e consult\r\n-Type 1e consult...     False    False   
11086  Samenvatting: \nDecursus\r\n-Type decursus: De...     False    False   
11087  Samenvatting: \nVerpleegkundige verslaglegging...     False    False   
11088  Samenvatting: \nMedisch Dossier\r\n[ Vk Sputov...     False    False   
11089  Samenvatting: \nVerpleegkundige verslaglegging...     False    False   

       has_agib2  has_gib_symptoms  has_scopie_reference  has_gib_treatment  
0          False              True                  True               True  
1          False              True                  True               True  
2          False              True                  True               True  
3          False              True                  True               True  
4          False              True                  True               True  
...          ...               ...                   ...                ...  
11085      False             False                  True              False  
11086      False             False                 False              False  
11087      False             False                 False              False  
11088      False             False                 False              False  
11089      False             False                 False              False  

[11090 rows x 10 columns]

In [206]:
df_measures['has_agib2'].value_counts()

False    11090
Name: has_agib2, dtype: int64

In [207]:
df_measures['has_gib_symptoms'].value_counts()

False    9140
True     1950
Name: has_gib_symptoms, dtype: int64

In [208]:
print('has_gib_symptoms: \n', df_measures['has_gib_symptoms'].value_counts())
print('has_scopie_reference: \n', df_measures['has_scopie_reference'].value_counts())
print('has_gib_treatment: \n', df_measures['has_gib_treatment'].value_counts())

has_gib_symptoms: 
 False    9140
True     1950
Name: has_gib_symptoms, dtype: int64
has_scopie_reference: 
 False    7822
True     3268
Name: has_scopie_reference, dtype: int64
has_gib_treatment: 
 False    7810
True     3280
Name: has_gib_treatment, dtype: int64


In [209]:
def extract_context(text, pattern, window=5):
    text = text.lower()
    matches = []
    for match in pattern.finditer(text):
        start, end = match.start(), match.end()
        before = text[:start]
        after = text[end:]
        before_words = re.findall(r'\w+', before)[-window:]
        after_words = re.findall(r'\w+', after)[:window]
        context = ' '.join(before_words + [match.group()] + after_words)
        matches.append(context)
    return matches[0] if matches else None

def extract_match(text, pattern):
    match = pattern.search(text.lower())
    return match.group() if match else None

def check_findings_pos(df, text_column, terms, new_column_name='has_findings'):
    pattern_str = "|".join([fr"\b{t}\b" if " " not in t and "[- ]" not in t else t for t in terms])
    pattern = re.compile(pattern_str, re.IGNORECASE)

    df[new_column_name + '_mention' ] = df[text_column].apply(lambda x: bool(pattern.search(str(x))))

    df[new_column_name + '_match'] = df[text_column].apply(
    lambda x: extract_match(str(x), pattern)    )

    df[new_column_name + '_context'] = df['verslagen_report_content'].apply(
    lambda x: extract_context(str(x), pattern)    )

    



In [210]:
# pattern_str = "|".join([fr"\b{t}\b" if " " not in t and "[- ]" not in t else t for t in gib_terms])
# gib_pattern = re.compile(pattern_str, re.IGNORECASE)

# df_measures['agib_mention'] = df_measures['verslagen_report_content'].apply(
#     lambda x: bool(gib_pattern.search(str(x)))
# )

# df_measures['agib_match'] = df_measures['verslagen_report_content'].apply(
#     lambda x: extract_match(str(x), gib_pattern)
# )

# df_measures['agib_context'] = df_measures['verslagen_report_content'].apply(
#     lambda x: extract_context(str(x), gib_pattern)
# )

check_findings_pos(df_measures, 'verslagen_report_content', agib_terms, new_column_name='agib')
check_findings_pos(df_measures, 'verslagen_report_content', gib_terms, new_column_name='gib')

In [211]:
df_measures.head()

pseudo_id verslagen_report_start_date  \
0  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 15:06:00   
1  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 09:53:00   
2  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 14:13:00   
3  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 13:48:00   
4  046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 08:47:00   

    verslagen_report_specialism  \
0  Maag-, Darm- en Leverziekten   
1  Maag-, Darm- en Leverziekten   
2  Maag-, Darm- en Leverziekten   
3  Maag-, Darm- en Leverziekten   
4  Maag-, Darm- en Leverziekten   

                            verslagen_report_content  has_agib  has_gib  \
0  Dhr. A.J. Dingemans, huisarts\r\n[STREETNAME] ...     False     True   
1  Samenvatting: \nRectaal bloedverlies obv diver...     False     True   
2  COLOSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] [L...     False     True   
3  GASTROSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] ...     False     True   
4  Samenvatting: \nRectaal bloedverlies ; eenmali...     False     True   

   has_agib2  has_gib_symptoms  has_scopie_reference  has_gib_treatment  \
0      False              True                  True               True   
1      False              True                  True               True   
2      False              True                  True               True   
3      False              True                  True               True   
4      False              True                  True               True   

   agib_mention agib_match agib_context  gib_mention           gib_match  \
0         False       None         None         True              melena   
1         False       None         None         True  divertikelbloeding   
2         False       None         None         True              melena   
3         False       None         None         True              melena   
4         False       None         None         True  divertikelbloeding   

                                         gib_context  
0  spontane conversie naar sinusritme 2016 melena...  
1  samenvatting rectaal bloedverlies obv divertik...  
2  t kamphuis indicatie bloedverlies rectaal mele...  
3  verwijzer j t kamphuis indicatie melena en blo...  
4  stabiel inr 2 8 wd divertikelbloeding dd toch ...

In [224]:
agib_terms_neg = [
    r"acute gi\s*bloeding",                       
    r"acute maagdarmbloeding",                    
    r"acute gastro[-\s]?intestinale bloeding",    
    r" agib "
]

agib_terms_MDL_neg = agib_terms_neg + [
    r"acute bloeding",               
    r"massaal bloedverlies",         
    r"shock door bloeding",          
    r"spoed scopie",                 
    r"hematemesis",                  
    r"melaena met hypotensie"        
]

gib_terms_neg = [
    r"mel[ae]na",                        
    r"hematemesis",                      
    r"hematochez[iy]e",                  
    r"rectaal bloed",                    
    r"rectaal verlies",                  
    r"zwart(e)? ontlasting",             
    r"bloed in ontlasting",              
    r"divertikelbloeding",               
    r"(bloed)?stolsels",                 
    r"gastro[-\s]?intestinale bloeding", 
    r"hemorragie"
]

gib_terms_MDL_neg = gib_terms_neg + [
    r"bloedverlies",               
    r"vers bloed per anum",        
    r"bloedende divertikels?",     
    r"maagdarmbloeding",           
    r"invloed van antistolling",   
    r"hemoglobinedaling",          
    r"bloedende ulcus",            
    r"bloedend varices?"
]

# def match_terms_neg(text, patterns):
#     text = text.lower()
#     return any(pattern.search(text) for pattern in patterns)

def match_terms_neg(text, pattern):
    text = text.lower()
    return bool(pattern.search(text))



def match_term_per_specialism_neg(
    df, 
    text_column, 
    terms, 
    terms_MDL, 
    negation_triggers, 
    new_column_name='new_column', 
    specialism_column='verslagen_report_specialism', 
    specialism_value='Maag-, Darm- en Leverziekten'
):
    # Create bleeding target patterns
    # bleeding_targets = "(" + "|".join(terms) + ")"
    # bleeding_targets_MDL = "(" + "|".join(terms_MDL) + ")"
    bleeding_targets = "(" + "|".join(re.escape(term) for term in terms) + ")"
    bleeding_targets_MDL = "(" + "|".join(re.escape(term) for term in terms_MDL) + ")"

    negation_pattern = re.compile('|'.join(negation_triggers))
    negation_pattern_MDL = re.compile('|'.join(negation_triggers))

    for i in range(len(df)):
        if df[specialism_column][i] == specialism_value:
            # negation_pattern = negation_pattern_MDL
            # bleeding_targets = bleeding_targets_MDL
            text = df[text_column].iloc[i]
            print(f"MDL: {text}")
            negated = bool(negation_pattern_MDL.search(str(text)))
            print(f"MDL negated: {negated}")
            df.at[i, 'negated'] = negated
            if negated:
                print(f"MDL negated match: {extract_match(str(text), negation_pattern_MDL)}")
                print(f"MDL negated context: {extract_context(str(text), negation_pattern_MDL)}")
                   
    else:
        # negation_pattern = negation_pattern
        # bleeding_targets = bleeding_targets
        text = df[text_column].iloc[i]
        print(f"Other: {text}")
        negated = bool(negation_pattern.search(str(text)))
        print(f"Other negated: {negated}")
        df.at[i, 'negated'] = negated

    # df['alltext'].apply(lambda x: bool(negation_pattern.search(str(x))))

#     # Compile negation patterns
#     negation_pattern = re.compile(
#         fr"{negation_triggers}(\W+\w+){{0,8}}?{bleeding_targets}|{bleeding_targets}(\W+\w+){{0,8}}?{negation_triggers}",
#         flags=re.IGNORECASE
#     )
#     negation_pattern_MDL = re.compile(
#         fr"{negation_triggers}(\W+\w+){{0,8}}?{bleeding_targets_MDL}|{bleeding_targets_MDL}(\W+\w+){{0,8}}?{negation_triggers}",
#         flags=re.IGNORECASE
#     )

#     sample = "De patiënt heeft geen aanwijzing voor acute gastro-intestinale bloeding."
#     print(bool(negation_pattern.search(sample)))  # Should be True


# #     df[new_column_name] = df.apply(
# #     lambda row: match_terms(row[text_column], negation_pattern_MDL.search(str(row[text_column]))) if row[specialism_column] == specialism_value else match_terms(row[text_column], negation_pattern.search(str(row[text_column]))),
# #     axis=1
# # )

#     df[new_column_name] = df.apply(
#         lambda row: match_terms_neg(row[text_column], negation_pattern_MDL) if row[specialism_column] == specialism_value else match_terms_neg(row[text_column], negation_pattern),
#         axis=1
#     )


    # # compile a single pattern (maybe joined with | if multiple terms)
    # negation_pattern = re.compile('|'.join(negation_triggers))
    # negation_pattern_MDL = re.compile('|'.join(negation_triggers))

    # df[new_column_name] = df.apply(
    #     lambda row: match_terms_neg(row[text_column], negation_pattern_MDL) if row[specialism_column] == specialism_value else match_terms_neg(row[text_column], negation_pattern),
    #     axis=1
    # )




In [225]:
# Combine both AGIB and GIB terms (general versions only)
bleeding_targets_list = "(" + "|".join(agib_terms_neg + gib_terms_neg) + ")"
bleeding_target_list_MDL = "(" + "|".join(agib_terms_MDL_neg + gib_terms_MDL_neg) + ")"

match_term_per_specialism_neg(df_measures, 'verslagen_report_content', bleeding_target_list, bleeding_target_list_MDL, negation_triggers, new_column_name='has_(a)gib_negation', specialism_column='verslagen_report_specialism', specialism_value='Maag-, Darm- en Leverziekten')

MDL: Dhr. A.J. Dingemans, huisarts
[STREETNAME] NR  [CITY]





datum
29-11-2020
kenmerk
0007475372 / [PATIENTID]
BSN nr.
[BSN]
betreft
mevrouw [INITIALS] [LASTNAME], geb. [BIRTHDATE] (87)
[STREETNAME], [ZIP]  [CITY]
tel. [PHONENUMBER]

 
Geachte collega,

Bovengenoemde patiënte was opgenomen van 24-11-2020 tot en met 26-11-2020 op de afdeling Maag-, Darm- en Leverziekten in verband met melaena en rectaal bloedverlies. 

Voorgeschiedenis
2002 Diep veneuze trombose en longembolie
2013 Cholecystectomie
2015 Diverticulitis
2016 Atriumfibrilleren met spontane conversie naar sinusritme
2016 Melena, waarvoor geen verklaring werd gevonden. In verband met stabiel Hb en in overleg met patiënte expectatief beleid. 
2018 Vermoeidheid bij sinusbradycardie waarvoor stop metoprolol en tambocor. 

Anamnese
Vanmiddag rond 13.30u fors helderrood bloedverlies met stolsels. Vermengd met ontlasting, mogelijk was deze zwart van kleur. Sinds 5 dagen zeurende pijn in de bovenbuik; maagpijn, waarvoor ze is ge

In [220]:
import re

# agib_terms = [
#     r"acute gi\s*bloeding",                       
#     r"acute maagdarmbloeding",                    
#     r"acute gastro[-\s]?intestinale bloeding",    
#     r" agib "
# ]


negation_triggers = r"(geen|niet|zonder|uitsluiten|ontkent|ontkend|ontkennen|negatief voor|geen aanwijzing voor|kan uitgesloten worden|geen tekenen van)"
bleeding_targets = "(" + "|".join(agib_terms_neg) + ")"

negation_pattern = re.compile(
    fr"{negation_triggers}(\W+\w+){{0,8}}?{bleeding_targets}|{bleeding_targets}(\W+\w+){{0,8}}?{negation_triggers}",
    flags=re.IGNORECASE
)


text = "De patiënt heeft geen aanwijzing voor acute gastro-intestinale bloeding."
print(bool(negation_pattern.search(text)))  # This MUST be True


False


In [226]:
df_measures['has_(a)gib_negation'].value_counts()

True    11090
Name: has_(a)gib_negation, dtype: int64

In [ ]:
sample = "Patiënt heeft geen tekenen van bloeding in de maag of rectaal verlies."
print(bool(negation_pattern.search(sample)))


test_pattern = re.compile(r"(geen|niet|zonder)\W{0,20}(bloeding|melena|hematemesis)", re.IGNORECASE)
print(bool(test_pattern.search(sample)))


False
False


In [ ]:
import re

# Raw regex terms - don't escape these
agib_terms = [
    r"acute gi\s*bloeding",                       
    r"acute maagdarmbloeding",                    
    r"acute gastro[-\s]?intestinale bloeding",    
    r"agib"
]

negation_triggers = r"(geen|niet|zonder|uitsluiten|ontkent|ontkend|ontkennen|negatief voor|geen aanwijzing voor|kan uitgesloten worden|geen tekenen van)"

# Combine into regex group
bleeding_targets = "(" + "|".join(agib_terms) + ")"

# ✅ Better inter-word pattern
between_words = r"(?:\s*\w+){0,8}"

# Compile final pattern
negation_pattern = re.compile(
    fr"{negation_triggers}{between_words}?{bleeding_targets}|{bleeding_targets}{between_words}?{negation_triggers}",
    flags=re.IGNORECASE
)
# ✅ Test string
sample = "De patiënt heeft geen aanwijzing voor acute gastro-intestinale bloeding."
print(bool(negation_pattern.search(sample)))  # ✅ Should now return True

# Optional: Show the match
match = negation_pattern.search(sample)
if match:
    print("✅ Matched:", match.group())


False


In [ ]:
# df_measures['negated'] = df_measures['verslagen_report_content'].apply(lambda x: bool(negation_pattern.search(str(x))))


In [ ]:
print(df_measures['negated'].value_counts())


False    10921
True       169
Name: negated, dtype: int64


In [ ]:
# for i, row in df_measures.iterrows():
#     text = str(row['verslagen_report_content']).lower()
#     if 'bloeding' in text:  # crude filter to find candidate texts
#         if negation_pattern.search(text):
#             print(f"\nNegated Match at row {i}:")
#             print(text)


In [ ]:
df_measures[df_measures['negated'] == True].head(5)

pseudo_id verslagen_report_start_date  \
0    046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-26 15:06:00   
2    046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 14:13:00   
4    046D1FFEBDD40E1665D0ABA6DD8FC9F8BC4351C6         2020-11-25 08:47:00   
104  088C9FD98B8B2CBCB597C17C07AC1845B21F0849         2023-01-14 13:34:00   
380  0BC512A65442D0BB4B00FBE05E7EA6283E5C11FD         2016-03-23 14:02:00   

      verslagen_report_specialism  \
0    Maag-, Darm- en Leverziekten   
2    Maag-, Darm- en Leverziekten   
4    Maag-, Darm- en Leverziekten   
104  Maag-, Darm- en Leverziekten   
380           Interne Geneeskunde   

                              verslagen_report_content  has_gib_symptoms  \
0    Dhr. A.J. Dingemans, huisarts\r\n[STREETNAME] ...              True   
2    COLOSCOPIE\r\n\r\nBetreft\r\nMw. [INITIALS] [L...              True   
4    Samenvatting: \nRectaal bloedverlies ; eenmali...              True   
104  Laatste samenvatting poliklinisch: \nMelaena o...              True   
380  Samenvatting: \n1e consult oncologie\r\n-Type ...             False   

     has_scopie_reference  has_gib_treatment  agib_mention agib_match  \
0                    True               True         False       None   
2                    True               True         False       None   
4                    True               True         False       None   
104                 False              False         False       None   
380                 False              False         False       None   

    agib_context  negated                                      negated_match  \
0           None     True  geen actieve bloedingsbron waardoor de werkdia...   
2           None     True  geen bloedingsbron gevonden.\r\nwaarschijnlijk...   
4           None     True  geen bloedingsbron gevonden.\nwaarschijnlijkhe...   
104         None     True  geen buikafwijkingen\nin verleden duodenumbloe...   
380         None     True              geen bloedneuzen gehad.\r\nnabloeding   

                                       negated_context  
0    uitgebreide diverticulose gezien werd en geen ...  
2    bij de klep bloeding gestopt geen bloedingsbro...  
4    bij de klep bloeding gestopt geen bloedingsbro...  
104  ontlasting bij lixiana goede tensie geen buika...  
380  wat bloedverlies spontaan verdwenen epistaxis ...

In [ ]:
df_measures['agib_final'] = df_measures['agib_mention'] & ~df_measures['negated']
len(df_measures[df_measures['agib_final'] == True]['pseudo_id'].unique())

0